# Project 2 - Earthquake Analysis

*Authors:* 
* *João Victor Barboza (victorxbarboza@gmail.com)* 
* *Thais Lins (thaisflins@gmail.com)* 
* *Vanessa Uchida (sayurivanessa@gmail.com)* 
* *Yuri Martins (yuri.alessandro.m@gmail.com)*



<center>
<img width="60" src="https://drive.google.com/uc?export=view&id=1JQRWCUpJNAvselJbC_K5xa5mcKl1gBQe"> 
</center>

In [2]:
# Uploading files from your local file system

from google.colab import files
uploaded = files.upload()
for fn in uploaded.keys():
  print('User uploaded file "{name}" with length {length} bytes'.format(
      name=fn, length=len(uploaded[fn])))

Saving earthquakes.csv to earthquakes.csv
User uploaded file "earthquakes.csv" with length 37534213 bytes


# 1 - Introduction

<center>
<img width="400" src="https://cdns.abclocal.go.com/content/wpvi/images/cms/1227365_1280x720.jpg"> 
</center>

> Earthquakes are any sudden shaking of the ground caused by the passage of seismic waves through Earth’s rocks. In its most general sense, the word earthquake is used to describe any seismic event (natural or caused by humans) that generates seismic waves. Earthquakes occur most often at geologic faults, narrow zones where rock masses move right along each another. The major fault lines of the world are located at the fringes of the huge tectonic plates that make up Earth’s crust.

> The goal of this notebook is to study, explore and analyze historically and geographically important information regarding earthquakes from 1980 to the current date. Such as the types of seismic events that occur most commonly or not in the world (earthquake, explosion, rock burst, nuclear explosion, etc), the magnitude and depth of earthquakes around the entire globe and whice areas are more prone to earthquakes with higher magnitudes. And finally,  an investigation will be done on the supposed relation between *supermoons* and seismic events.

> This notebook will explore data from two datasets, one dataset based solely on seismic events and the dates they occurred, their types, magnitude, as well as other information. The second dataset contains occurrence dates as well as basic information relating to supermoons. Other than that, a json file will be used for separating borders of countries in the maps (**countries_geojson.json**). These datasets are all available on [Github - Earthquake Analysis](https://github.com/thaislins/earthquake-analysis) and must be uploaded to this notebook in order for this analysis to be accurate.

> The dataset **earthquakes.csv** was downloaded from [USGS - Earthquake Catalog](https://earthquake.usgs.gov/earthquakes/search/), filtering the earthquake data from that of a magnitude higher than 4.5 and from the year 1980 to the current year.

> The dataset **supermoons.csv** was downloaded from [AstroPixels.com](http://astropixels.com/ephemeris/moon/fullperigee2001.html) and has dates from 2001 to the present year.

## 1.1 - Description of the dataset

The data below describes the columns of the dataset **earthquakes.csv**:

*   **time** - Time when the event occurred. Times are reported in milliseconds since the epoch ( 1970-01-01T00:00:00.000Z), and do not include leap seconds. In certain output formats, the date is formatted for readability
*  **latitude** - Decimal degrees latitude. Negative values for southern latitudes.
* **longitude** - Decimal degrees longitude. Negative values for western longitudes.
* **depth** - Depth of the event in kilometers.
* **mag** - The magnitude for the event.
* **magType** - The method or algorithm used to calculate the preferred magnitude for the event.
* **nst** - The total number of seismic stations used to determine earthquake location.
* **gap** - The largest azimuthal gap between azimuthally adjacent stations (in degrees). In general, the smaller this number, the more reliable is the calculated horizontal position of the earthquake. Earthquake locations in which the azimuthal gap exceeds 180 degrees typically have large location and depth uncertainties.
* **dmin** - Horizontal distance from the epicenter to the nearest station (in degrees). 1 degree is approximately 111.2 kilometers. In general, the smaller this number, the more reliable is the calculated depth of the earthquake.
* **rms** - The root-mean-square (RMS) travel time residual, in sec, using all weights. This parameter provides a measure of the fit of the observed arrival times to the predicted arrival times for this location. Smaller numbers reflect a better fit of the data. The value is dependent on the accuracy of the velocity model used to compute the earthquake location, the quality weights assigned to the arrival time data, and the procedure used to locate the earthquake.
* **net** - The ID of a data contributor. Identifies the network considered to be the preferred source of information for this event.
* **id** - A unique identifier for the event. This is the current preferred id for the event, and may change over time. See the "ids" GeoJSON format property.
* **updated** - Time when the event was most recently updated. Times are reported in milliseconds since the epoch. In certain output formats, the date is formatted for readability.
* **place** - Textual description of named geographic region near to the event. This may be a city name, or a Flinn-Engdahl Region name.
* **type** - A comma-separated list of product types associated to this event.
* **horizontalError** - Uncertainty of reported location of the event in kilometers. The horizontal location error, in km, defined as the length of the largest projection of the three principal errors on a horizontal plane. The principal errors are the major axes of the error ellipsoid, and are mutually perpendicular. The horizontal and vertical uncertainties in an event's location varies from about 100 m horizontally and 300 meters vertically for the best located events, those in the middle of densely spaced seismograph networks, to 10s of kilometers for global events in many parts of the world. We report an "unknown" value if the contributing seismic network does not supply uncertainty estimates.
* **depthError** - Uncertainty of reported depth of the event in kilometers. The depth error, in km, defined as the largest projection of the three principal errors on a vertical line.
* **magError** - Uncertainty of reported magnitude of the event. The estimated standard error of the magnitude. The uncertainty corresponds to the specific magnitude type being reported and does not take into account magnitude variations and biases between different magnitude scales. We report an "unknown" value if the contributing seismic network does not supply uncertainty estimates.
* **magNst** - The total number of seismic stations used to calculate the magnitude for this earthquake.
* **status** - Indicates whether the event has been reviewed by a human. Status is either automatic or reviewed. Automatic events are directly posted by automatic processing systems and have not been verified or altered by a human. Reviewed events have been looked at by a human. The level of review can range from a quick validity check to a careful reanalysis of the event.
* **locationSource** - The network that originally authored the reported location of this event.
* **magSource** - Network that originally authored the reported magnitude for this event.


# 2 - Installing packages and importing libraries

In [3]:
# install folium packages
!pip install folium
!pip install python-dateutil
!pip install isodate

    100% |████████████████████████████████| 81kB 3.0MB/s 
    100% |████████████████████████████████| 51kB 2.3MB/s 


In [0]:
# importing libraries
from pathlib import Path
from tqdm import tqdm
import os
import json
import pandas as pd
import folium
from folium.plugins import HeatMap, MarkerCluster, TimeSliderChoropleth
import branca
from folium import plugins
import numpy as np

#3 - Importing the dataset and verifying basic information

In [5]:
import pandas as pd

# read the dataset
earthquakes = pd.read_csv("earthquakes.csv")
earthquakes.head(5)

Unnamed: 0                      time  latitude  longitude  depth  mag  \
0           0  2018-10-26T04:00:48.340Z   37.3944    20.7602   10.0  4.5   
1           1  2018-10-26T03:14:36.750Z   44.6221   145.6544   10.0  4.7   
2           2  2018-10-26T03:04:53.700Z   44.5381   145.4010   10.0  5.6   
3           3  2018-10-26T02:36:06.540Z   37.4468    20.6759   10.0  4.7   
4           4  2018-10-26T02:28:43.300Z   37.2826    20.6045   10.0  4.5   

  magType  nst    gap   dmin    ...                       updated  \
0      mb  NaN  139.0  3.023    ...      2018-10-26T04:27:43.040Z   
1      mb  NaN  134.0  2.252    ...      2018-10-26T03:33:58.040Z   
2     mww  NaN   60.0  2.058    ...      2018-10-26T05:07:01.518Z   
3      mb  NaN  165.0  2.365    ...      2018-10-26T04:09:40.040Z   
4      mb  NaN  138.0  2.507    ...      2018-10-26T03:54:47.040Z   

                          place        type horizontalError depthError  \
0    36km S of Lithakia, Greece  earthquake             8.0        2.0   
1    63km NNW of Otrada, Russia  earthquake             6.1        1.9   
2     63km NW of Otrada, Russia  earthquake             7.0        1.8   
3  33km SSW of Lithakia, Greece  earthquake             6.8        1.9   
4  52km SSW of Lithakia, Greece  earthquake             8.0        1.9   

  magError  magNst    status  locationSource  magSource  
0    0.180     9.0  reviewed              us         us  
1    0.051   115.0  reviewed              us         us  
2    0.073    18.0  reviewed              us         us  
3    0.183     9.0  reviewed              us         us  
4    0.140    16.0  reviewed              us         us  

[5 rows x 23 columns]

In [6]:
earthquakes.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 209457 entries, 0 to 209456
Data columns (total 23 columns):
Unnamed: 0         209457 non-null int64
time               209457 non-null object
latitude           209457 non-null float64
longitude          209457 non-null float64
depth              209457 non-null float64
mag                209457 non-null float64
magType            209456 non-null object
nst                87625 non-null float64
gap                110710 non-null float64
dmin               37466 non-null float64
rms                200202 non-null float64
net                209457 non-null object
id                 209457 non-null object
updated            209457 non-null object
place              209452 non-null object
type               209457 non-null object
horizontalError    30235 non-null float64
depthError         95990 non-null float64
magError           35817 non-null float64
magNst             164656 non-null float64
status             209457 non-null object
l

## 3.1 - Parsing dates 

In [0]:
import dateutil.parser

earthquakes["time"] = earthquakes['time'].str[:10]
earthquakes["time"] = pd.to_datetime(earthquakes["time"])


## 3.2 - Visualizing tectonic plates



> Initially, we will plot markers on the world map that indicate where an earthquake has occurred to show which areas are most affected. Since earthquakes tend to happen most likely along geologic faults, it is known that closer to the border of tectonic plates, more earthquakes will be found. In this sense, by plotting a sample of earthquake markers on the map, it is almost possible to visualize the tectonic plates that exist in the earth.

In [6]:
earthquakes_set = earthquakes.sample(n=2800, random_state=1)

# Create a map object
m = folium.Map(
    location=[52.34167, 40.36472],
    zoom_start=2,
    tiles='OpenStreetMap'
)

for index, row in tqdm(earthquakes_set.iterrows()):
        # Draw a small circle
        folium.CircleMarker([row['latitude'], row['longitude']],
                    radius=2,
                    color='red').add_to(m)

m

2800it [00:00, 3145.08it/s]


# 4 - Analyzing seismic events by type

> Seismic events are not just earthquakes created because of tectonic plates movement, as we saw before. There are others events that can cause it - like volcanic eruption, rock burst or nuclear explosions. So, we are now going to plot on the map each seismic event and connect them to its type.

> In addition, we plot this map using cluster - that groups closer events. Because of this, it's easy also know what are the regions in the world that have the biggest number of seismic events.

> Each marker contains a label that show the seismic event's type and his year. We used two dictionaries to create the colors and the icons of the marker, based on seismic event type.

In [0]:
# Create a subset of the dataframe
earthquakes_subset = earthquakes.sample(n=1100, random_state=1)

In [0]:
# Dictionary for colors
unit_type_colors = {
    'earthquake': 'red',
    'volcanic eruption': 'yellow',
    'nuclear explosion': 'orange',
    'rock burst': 'grey',
    'explosion': 'blue',
    'other event': 'green',
}

# Dictionary for icons
unit_type_icons = {
    'earthquake': 'exclamation',
    'volcanic eruption': 'mountain',
    'nuclear explosion': 'skull-crossbones',
    'rock burst': 'chess-rook',
    'explosion': 'fire',
    'other event': 'otter',
}

In [10]:
# Ploting the earthquakes units on map
mc = MarkerCluster()
for index, row in tqdm(earthquakes_subset.iterrows()):
  mc.add_child(
      folium.Marker(
          [row['latitude'], row['longitude']],
          icon = folium.Icon(color = 'red',icon = unit_type_icons[row['type']], prefix='fa'),
          popup = "{}, {}".format(row['type'].capitalize(), row['time'].year)
      )
  )

1100it [00:00, 2604.03it/s]


In [11]:
# Create a map object
m = folium.Map(
    location=[52.34167, 40.36472],
    zoom_start=2,
    tiles='Stamen Terrain'
)
m.add_child(mc)
m

# 5 -   Analyzing earthquakes by magnitude

> Now we are going to work as before, but using earthquake's magnitude as the information rather than type. First of all, we need to know what is those numbers in the dataset. After this, we could reach the follow informations:


*   **Magnitude less than 2**: tremors captured only by seismographs;
*   **Between 2 and 3**: similar impact to the passage of a large and heavy vehicle;
*   **Between 3 and 4**: often felt but rarely causes damage;
*   **Between 4 and 5:** can cause significant damage to poorly designed buildings and restricted areas;
*   **Between 6 and 7:** destruction of fragile constructions;
*   **Between 7 and 8:** serious damage to buildings;
*   **Between 8 and 9:** destruction of bridges, viaducts;
*   **Above 9:** total destruction

> With this in hands, we could prepare two dictionaries to plot the marker with colors and icons from each magnitude category.




In [17]:
# Explore the mag column and discover what are his values
earthquakes["mag"].value_counts(sort=True)

4.50    38111
4.60    34830
4.70    29618
4.80    24127
4.90    18244
5.00    13759
5.10    10775
5.20     8802
5.30     6602
5.40     5387
5.50     4031
5.60     3190
5.70     2434
5.80     1795
5.90     1550
6.00     1219
6.10      931
6.20      707
6.30      614
6.40      469
6.50      370
6.60      288
6.70      242
6.80      182
6.90      156
7.00      117
7.10       98
7.20       76
7.30       50
7.40       41
        ...  
5.11        2
5.25        2
9.10        2
5.28        2
5.49        2
5.24        2
5.27        2
5.16        1
5.58        1
6.57        1
5.67        1
5.52        1
5.44        1
5.47        1
6.02        1
5.93        1
5.66        1
5.21        1
5.43        1
5.64        1
5.53        1
5.18        1
5.94        1
5.89        1
5.51        1
5.97        1
6.45        1
5.88        1
8.80        1
5.14        1
Name: mag, Length: 148, dtype: int64

In [0]:
# Dictionary for colors
unit_mag_colors = {
    2: 'lightgreen',   # tremores captados apenas por sismógrafos;
    3: 'green',        # impacto semelhante à passagem de um veículo grande e pesado;
    4: 'darkgreen',    # Frequentemente sentido, mas raramente causa danos;
    5: 'lightblue',    # Pode causar danos importantes em edifícios mal concebidos e em zonas restritas;
    6: 'blue',         # destruição de construções frágeis
    7: 'orange',       # danos graves em edifícios
    8: 'red',          # destruição de pontes, viadutos
    9: 'darkred'       # destruição total 
}

# Dictionary for icons
unit_mag_icons = {
    2: 'signal-1',               # tremores captados apenas por sismógrafos;
    3: 'signal-2',               # Frequentemente sentido, mas raramente causa danos;
    4: 'signal-2',               # impacto semelhante à passagem de um veículo grande e pesado;
    5: 'signal-2',               # Pode causar danos importantes em edifícios mal concebidos e em zonas restritas;
    6: 'signal-3',               # destruição de construções frágeis
    7: 'signal',                 # danos graves em edifícios
    8: 'exclamation-circle',     # destruição de pontes, viadutos
    9: 'exclamation-triangle'    # destruição total 
}

In [92]:
# Ploting the earthquakes units on map
mc = MarkerCluster()
for index, row in tqdm(earthquakes_subset.iterrows()):
  mag = round(row['mag'])
  mc.add_child(
      folium.Marker(
          [row['latitude'], row['longitude']],
          icon = folium.Icon(color = unit_mag_colors[mag], icon = unit_mag_icons[mag], prefix='fa'),
          popup = "{}, {}".format(row['mag'], row['time'].year)
      )
  )

1100it [00:00, 3115.43it/s]


In [93]:
# Create a map object
m = folium.Map(
    location=[52.34167, 40.36472],
    zoom_start=5,
    tiles='Mapbox Control Room'
)

m.add_child(mc)
m

# 6 -   Analyzing earthquakes by depth

> After viewing how earthquakes are distributed by magnitude worldwide, we will now analyze their distribution based on the depth of where the event started. 

In [0]:
earthquakes['depth'].value_counts()

In [0]:
earthquakes['country'] = earthquakes['place'].str.rsplit(',').str[-1] 

In [0]:
# load the data and use 'latin-1'encoding because the accent
countries_data = json.load(open('countries_geojson.json',encoding='latin-1'))

In [0]:
countries = []
# list all countries in the world
for country in countries_data['features']:
        countries.append(country['properties']['name'])

In [0]:
eqss = earthquakes.sample(n=2800, random_state=1)

# create a threshold of legend
threshold_scale = np.linspace(eqss['depth'].min(),
                              eqss['depth'].max(), 6, dtype=int).tolist()

choropleth_options = {
    'geo_data': countries_data,
    'data': eqss,
    'columns': ['country', 'depth'],
    'key_on': 'feature.properties.name',
    'fill_color': 'YlOrBr',
    'legend_name': 'Earthquake by depth (1980 - 2018)',
    'highlight': True,
    'threshold_scale': threshold_scale
}



In [86]:
# Create a map object
m = folium.Map(
    location=[52.34167, 40.36472],
    zoom_start=2,
    tiles='Mapbox Bright'
)

# Configure choropleth layer
m.choropleth(**choropleth_options)

# Configure geojson layer
folium.GeoJson(countries_data).add_to(m)

m

# 7 - Do supermoons increase the risk of earthquakes? Myth or Fact?

> A "supermoon" is a popular expression used to describe a full moon or a new moon that is orbiting at a relative distance to the earth that is greater than 0.9. Supermoons occur because the moon revolves around the earth in an elliptical orbit, instead of a circular one. Within this elliptical path there is a point when the moon is closest to the earth and a point when the moon is farthest away from the earth. These points are respectively referred to as a perigee and apogee.  

> Researchers  have been looking for a possible link between this unusual celestial event and earthquakes. It is claimed that  the increased gravitational force from the Moon, as it gets closer to Earth, could cause fault lines to trigger catastrophic earthquakes on land or in the ocean. 

> For this reason, we will explore a new dataset containing dates of supermoons from 2001 to the current date, and analyze whether or not there is a correlation between these two events and earthquakes.









## 7.1 - Description of the dataset to be used

The data below describes the columns of the dataset **supermoons.csv**:

*   **Year** - Year that the supermoon occurred.
*  **Full Moon** - Date that indicates when the supermoon occurred. A letter following the Full Moon date indicates that a lunar eclipse occurs 
    * **t** - Total eclipse
    * **p** - Partial eclipse
    * **n** - Penumbral eclipse
* **Distance (km)** -  Moon's geocentric distance in kilometers.
* **Diameter (arc-min)** - the geocentric apparent diameter of the Moon (in arc-minutes).
* **Relative Distance** - expresses the distance of the Full Moon (Dfm) with respect to apogee (Da) and perigee (Dp) distances of that current orbit. 
      Relative Distance = (Da - Dfm)/(Da - Dp)
* **Relative Brightess** - composed of two values that express the brightness of the Full Moon relative to its brightness at the current apogee (left) and at its mean distance (right).
* **Perigee** - Date of when moon was at 90% of its closest approach to Earth in a given orbit.
* **Delta Perigee (days)** - the time difference (in days) between nearest perigee and Full Moon.

## 7.2 - Importing and analyzing the dataset

In [31]:
supermoons = pd.read_csv("supermoons.csv", sep = ",")
supermoons.head(5)

Year      Full Moon  Distance (km)  Diameter (arc-min)  Relative Distance  \
0  2001  Jan 09  20:24         357406               33.43              0.994   
1  2001  Feb 08  07:12         356994               33.47              0.997   
2  2001  Mar 09  17:23         361389               33.07              0.965   
3  2002  Jan 28  22:50         361766               33.03              0.961   
4  2002  Feb 27  09:17         357091               33.46              0.996   

  Relative Brightness        Perigee  Delta Perigee (days)  
0         1.292/1.157  Jan 10  08:59                 0.524  
1         1.295/1.159  Feb 07  22:19                 0.370  
2         1.259/1.131  Mar 08  08:55                 1.353  
3         1.256/1.129  Jan 30  09:02                 1.424  
4         1.295/1.159  Feb 27  19:47                 0.438

In [109]:
supermoons.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 71 entries, 0 to 70
Data columns (total 8 columns):
 Year                   71 non-null int64
Full Moon               71 non-null object
Distance (km)           71 non-null int64
Diameter (arc-min)      71 non-null float64
Relative Distance       71 non-null float64
Relative Brightness     71 non-null object
Perigee                 71 non-null object
Delta Perigee (days)    71 non-null float64
dtypes: float64(3), int64(2), object(3)
memory usage: 4.5+ KB


## 7.3 - Parsing dates 

> After analyzing and obtaining some basic information from the dataset, we will now take focus into the date that these supermoons occurred and parse these dates so that we may, later on, compare them to the dates that earthquakes occurred. Finally, we evaluate, based on an estimation, if there is an actual connection surrounding these events.

In [0]:
#Define function to convert to timestamp
def convert_date(year, month_day):
     new_date = dateutil.parser.parse(str(year) + " " + month_day)
     return new_date

#Apply date conversion function to columns
supermoons["Date"] = supermoons.apply(lambda x: convert_date(x["Year"],x["Full Moon"]), axis=1)
supermoons["Date"] = supermoons["Date"].dt.floor("D")
supermoon_dates = supermoons["Date"].tolist()

## 7.4 - Filtering the years with the most earthquakes

> After comparing the dates of the supermoons and earthquakes, we created a new dataset of earthquakes that contains only earthquakes that happened on dates in which the supermoon occurred. With this new dataset, we investigated and chose to plot the years that had the most earthquakes.

In [0]:
# Filter dataframe
supermoon_earthquake = earthquakes[earthquakes['time'].isin(supermoon_dates)]

In [36]:
# Analyze which years have the most earthquakes
supermoon_earthquake['time'].dt.year.value_counts()

2010    196
2011    141
2016     98
2014     94
2015     91
2012     82
2007     74
2013     73
2017     69
2009     65
2004     62
2003     62
2006     57
2005     54
2018     42
2008     38
2002     36
2001     34
Name: time, dtype: int64

In [90]:
# Filter dataframe to obtain only dates from 2010
supermoon_earthquake_2010 = supermoon_earthquake[(supermoon_earthquake['time'].dt.year == 2010)]
print(supermoon_earthquake_2010['time'].unique())

# Create a map object
m = folium.Map(
    location=[52.34167, 40.36472],
    zoom_start=2,
    tiles='Mapbox Bright'
)

for index, row in tqdm(supermoon_earthquake_2010.iterrows()):
        # Draw a small circle
        folium.CircleMarker([row['latitude'], row['longitude']],
                    radius=5,
                    color='blue').add_to(m)
      
m

196it [00:00, 3662.05it/s]

['2010-03-30T00:00:00.000000000' '2010-02-28T00:00:00.000000000'
 '2010-01-30T00:00:00.000000000']


In [88]:
supermoon_earthquake_2010["mag"].value_counts()

4.6    36
4.5    35
4.7    27
4.9    20
4.8    19
5.0    16
5.2    13
5.1    13
5.3     7
5.4     3
5.9     2
5.6     2
6.2     1
5.7     1
6.6     1
Name: mag, dtype: int64

In [69]:
# Filter dataframe to obtain only dates from 2011
supermoon_earthquake_2011 = supermoon_earthquake[(supermoon_earthquake['time'].dt.year == 2011)]
print(supermoon_earthquake_2011['time'].unique())
print(len(supermoon_earthquake_2011))

# Create a map object
m = folium.Map(
    location=[52.34167, 40.36472],
    zoom_start=2,
    tiles='Mapbox Bright'
)

for index, row in tqdm(supermoon_earthquake_2011.iterrows()):
        # Draw a small circle
        folium.CircleMarker([row['latitude'], row['longitude']],
                    radius=5,
                    color='red').add_to(m)

m

141it [00:00, 3508.61it/s]

['2011-05-17T00:00:00.000000000' '2011-04-18T00:00:00.000000000'
 '2011-03-19T00:00:00.000000000' '2011-02-18T00:00:00.000000000'
 '2011-01-19T00:00:00.000000000']
141


In [89]:
supermoon_earthquake_2011["mag"].value_counts()

4.60    37
4.50    25
4.70    20
4.80    19
4.90    11
5.10     6
5.00     5
5.20     4
5.30     4
5.70     3
5.40     3
5.90     1
6.60     1
5.09     1
5.50     1
Name: mag, dtype: int64

## 7.5 - Conclusion

> Now that we have inspected this new dataframe (**supermoon_earthquake**) and chosen to investigate the years with the most earthquakes, we are able to make a few conclusions, though it is believed to be necessary to analyze a great deal of factors before making any real assumptions on the correlation between these events. 

> First off, we can conclude that a great deal of earthquakes occurred in these dates, considering that only 2010 had only 3 supermoons and 2011 had 5 supermoons and each had 196 and 141 earthquakes, respectively. This is a great deal of earthquakes for such a small amount of dates, so, likewise, we have a tendency to suppose that supermoons really do affect earthquakes. However, it is important to check the magnitude of these earthquakes to see if they were stronger. After veryfing such data, we concluded that a great deal of them were in the scale of 4.5 - 5.0 in the richter scale. This is a medium value for the magnitude of an earthquake, and while a seismic event of this scale can cause negative effects in a few places, others may not be affected. 